In [1]:
import numpy as np
import pandas as pd

import pandas_profiling
from paramsearch import paramsearch

from sklearn.model_selection import train_test_split

from sklearn.ensemble import RandomForestClassifier
from catboost import Pool, CatBoostClassifier

In [2]:
df = pd.read_csv("../data/train.csv")
df.head()

Loan_ID Gender Married Dependents     Education Self_Employed  \
0  LP001002   Male      No          0      Graduate            No   
1  LP001003   Male     Yes          1      Graduate            No   
2  LP001005   Male     Yes          0      Graduate           Yes   
3  LP001006   Male     Yes          0  Not Graduate            No   
4  LP001008   Male      No          0      Graduate            No   

   ApplicantIncome  CoapplicantIncome  LoanAmount  Loan_Amount_Term  \
0             5849                0.0         NaN             360.0   
1             4583             1508.0       128.0             360.0   
2             3000                0.0        66.0             360.0   
3             2583             2358.0       120.0             360.0   
4             6000                0.0       141.0             360.0   

   Credit_History Property_Area Loan_Status  
0             1.0         Urban           Y  
1             1.0         Rural           N  
2             1.0         Urban           Y  
3             1.0         Urban           Y  
4             1.0         Urban           Y

In [3]:
# df.profile_report(style={'full_width':True})

In [4]:
df.dtypes

Loan_ID               object
Gender                object
Married               object
Dependents            object
Education             object
Self_Employed         object
ApplicantIncome        int64
CoapplicantIncome    float64
LoanAmount           float64
Loan_Amount_Term     float64
Credit_History       float64
Property_Area         object
Loan_Status           object
dtype: object

In [5]:
# df[df["Dependents"] == "3+"] = "3"
# df[df["Dependents"].isnull()] = "0"

In [6]:
df.Dependents.unique()

array(['0', '1', '2', '3+', nan], dtype=object)

In [7]:
# df["Dependents"] = df["Dependents"].astype(int)

In [8]:
# df[df["Credit_History"].isnull()] = "0"
# df["Credit_History"] = df["Credit_History"].astype(int)

In [9]:
df.iloc[:,np.where(df.dtypes == "object")[0]] = df.iloc[:,np.where(df.dtypes == "object")[0]].astype(str)

In [10]:
df = df.fillna(df.mean())

In [11]:
features = ["ApplicantIncome", "CoapplicantIncome", "Loan_Amount_Term", "Credit_History"]
# X = df.drop("Loan_Status", axis=1)
X = df.drop(["Loan_ID", "Loan_Status"], axis=1)
# X = df[features]
y = df["Loan_Status"]
X.dtypes

Gender                object
Married               object
Dependents            object
Education             object
Self_Employed         object
ApplicantIncome        int64
CoapplicantIncome    float64
LoanAmount           float64
Loan_Amount_Term     float64
Credit_History       float64
Property_Area         object
dtype: object

In [12]:
categorical_features_indices = np.where(X.dtypes == "object")[0]
categorical_features_indices

array([ 0,  1,  2,  3,  4, 10])

In [13]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.33, random_state=42)

In [24]:
params = {'depth':[3,1,2,6,4,5,7,8,9,10],
          'iterations':[250,100,500,1000, 1500],
          'learning_rate':[0.001,0.01, 0.1,0.2,0.3], 
          'l2_leaf_reg':[3,1,5,10,100],
          'border_count':[32,5,10,20,50,100,200],
#           'ctr_border_count':[50,5,10,20,100,200],
          'thread_count':4}

In [25]:
# this function does 3-fold crossvalidation with catboostclassifier          
def crossvaltest(params,train_set,train_label,cat_dims,n_splits=3):
    kf = KFold(n_splits=n_splits,shuffle=True) 
    res = []
    for train_index, test_index in kf.split(train_set):
        train = train_set.iloc[train_index,:]
        test = train_set.iloc[test_index,:]

        labels = train_label.ix[train_index]
        test_labels = train_label.ix[test_index]

        clf = CatBoostClassifier(loss_function='MultiClass', **params)
#         print(train)
#         print(labels)
        clf.fit(train, labels, cat_features=cat_dims)
#         clf.fit(train, np.ravel(labels), cat_features=cat_dims)

        res.append(np.mean(clf.predict(test)==np.ravel(test_labels)))
    return np.mean(res)

In [16]:
from itertools import product,chain
from sklearn.model_selection import KFold

In [26]:
# this function runs grid search on several parameters
def catboost_param_tune(params,train_set,train_label,cat_dims=None,n_splits=5):
    ps = paramsearch(params)
    # search 'border_count', 'l2_leaf_reg' etc. individually 
    #   but 'iterations','learning_rate' together
    for prms in chain(ps.grid_search(['border_count']),
#                       ps.grid_search(['ctr_border_count']),
                      ps.grid_search(['l2_leaf_reg']),
                      ps.grid_search(['iterations','learning_rate']),
                      ps.grid_search(['depth'])):
        res = crossvaltest(prms,train_set,train_label,cat_dims,n_splits)
        # save the crossvalidation result so that future iterations can reuse the best parameters
        ps.register_result(res,prms)
        print(res,prms, 'best:',ps.bestscore(),ps.bestparam())
    return ps.bestparam()

bestparams = catboost_param_tune(params,X, y, categorical_features_indices)


/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:9: DeprecationWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/indexing.html#ix-indexer-is-deprecated
  if __name__ == '__main__':
/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:10: DeprecationWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/indexing.html#ix-indexer-is-deprecated
  # Remove the CWD from sys.path while we load stuff.


0:	learn: 0.6927781	total: 936us	remaining: 233ms
1:	learn: 0.6924779	total: 1.78ms	remaining: 221ms
2:	learn: 0.6921166	total: 2.7ms	remaining: 222ms
3:	learn: 0.6917527	total: 3.55ms	remaining: 218ms
4:	learn: 0.6913922	total: 4.39ms	remaining: 215ms
5:	learn: 0.6910262	total: 5.3ms	remaining: 216ms
6:	learn: 0.6906665	total: 6.17ms	remaining: 214ms
7:	learn: 0.6903011	total: 7.05ms	remaining: 213ms
8:	learn: 0.6899343	total: 7.92ms	remaining: 212ms
9:	learn: 0.6895761	total: 8.82ms	remaining: 212ms
10:	learn: 0.6892025	total: 9.49ms	remaining: 206ms
11:	learn: 0.6888393	total: 10.3ms	remaining: 205ms
12:	learn: 0.6884722	total: 11.2ms	remaining: 204ms
13:	learn: 0.6881870	total: 12.1ms	remaining: 203ms
14:	learn: 0.6878225	total: 12.9ms	remaining: 202ms
15:	learn: 0.6874755	total: 13.8ms	remaining: 201ms
16:	learn: 0.6871182	total: 14.6ms	remaining: 200ms
17:	learn: 0.6867493	total: 15.2ms	remaining: 196ms
18:	learn: 0.6863953	total: 16.1ms	remaining: 195ms
19:	learn: 0.6860429	tota

215:	learn: 0.6278454	total: 183ms	remaining: 28.8ms
216:	learn: 0.6275985	total: 184ms	remaining: 28ms
217:	learn: 0.6273441	total: 185ms	remaining: 27.1ms
218:	learn: 0.6270862	total: 186ms	remaining: 26.3ms
219:	learn: 0.6268287	total: 187ms	remaining: 25.5ms
220:	learn: 0.6266267	total: 187ms	remaining: 24.6ms
221:	learn: 0.6263701	total: 188ms	remaining: 23.7ms
222:	learn: 0.6261236	total: 189ms	remaining: 22.9ms
223:	learn: 0.6258679	total: 189ms	remaining: 22ms
224:	learn: 0.6256167	total: 190ms	remaining: 21.1ms
225:	learn: 0.6254190	total: 191ms	remaining: 20.3ms
226:	learn: 0.6251738	total: 192ms	remaining: 19.5ms
227:	learn: 0.6249274	total: 193ms	remaining: 18.6ms
228:	learn: 0.6246801	total: 194ms	remaining: 17.8ms
229:	learn: 0.6244309	total: 195ms	remaining: 17ms
230:	learn: 0.6241804	total: 196ms	remaining: 16.1ms
231:	learn: 0.6239335	total: 197ms	remaining: 15.3ms
232:	learn: 0.6236837	total: 198ms	remaining: 14.4ms
233:	learn: 0.6234343	total: 199ms	remaining: 13.6ms

212:	learn: 0.6265384	total: 184ms	remaining: 31.9ms
213:	learn: 0.6262756	total: 185ms	remaining: 31.1ms
214:	learn: 0.6260183	total: 186ms	remaining: 30.3ms
215:	learn: 0.6257576	total: 187ms	remaining: 29.4ms
216:	learn: 0.6254972	total: 188ms	remaining: 28.6ms
217:	learn: 0.6252810	total: 189ms	remaining: 27.7ms
218:	learn: 0.6250220	total: 190ms	remaining: 26.9ms
219:	learn: 0.6247614	total: 191ms	remaining: 26ms
220:	learn: 0.6244989	total: 192ms	remaining: 25.2ms
221:	learn: 0.6242394	total: 193ms	remaining: 24.3ms
222:	learn: 0.6240215	total: 194ms	remaining: 23.4ms
223:	learn: 0.6237654	total: 195ms	remaining: 22.6ms
224:	learn: 0.6235071	total: 196ms	remaining: 21.7ms
225:	learn: 0.6232562	total: 196ms	remaining: 20.9ms
226:	learn: 0.6230401	total: 197ms	remaining: 20ms
227:	learn: 0.6228187	total: 198ms	remaining: 19.1ms
228:	learn: 0.6226017	total: 199ms	remaining: 18.2ms
229:	learn: 0.6223403	total: 200ms	remaining: 17.4ms
230:	learn: 0.6220801	total: 201ms	remaining: 16.5

187:	learn: 0.6366091	total: 183ms	remaining: 60.4ms
188:	learn: 0.6363465	total: 184ms	remaining: 59.4ms
189:	learn: 0.6361441	total: 186ms	remaining: 58.6ms
190:	learn: 0.6358831	total: 187ms	remaining: 57.6ms
191:	learn: 0.6356346	total: 187ms	remaining: 56.6ms
192:	learn: 0.6353745	total: 188ms	remaining: 55.5ms
193:	learn: 0.6351725	total: 189ms	remaining: 54.5ms
194:	learn: 0.6349157	total: 190ms	remaining: 53.5ms
195:	learn: 0.6346586	total: 191ms	remaining: 52.6ms
196:	learn: 0.6344102	total: 192ms	remaining: 51.7ms
197:	learn: 0.6342009	total: 193ms	remaining: 50.7ms
198:	learn: 0.6339457	total: 194ms	remaining: 49.8ms
199:	learn: 0.6336967	total: 195ms	remaining: 48.8ms
200:	learn: 0.6334504	total: 196ms	remaining: 47.8ms
201:	learn: 0.6332430	total: 197ms	remaining: 46.9ms
202:	learn: 0.6329894	total: 198ms	remaining: 45.9ms
203:	learn: 0.6327342	total: 200ms	remaining: 45ms
204:	learn: 0.6324793	total: 201ms	remaining: 44.1ms
205:	learn: 0.6322309	total: 202ms	remaining: 43

...

277:	learn: 0.6131478	total: 2.87s	remaining: 7.45s
278:	learn: 0.6129307	total: 2.91s	remaining: 7.52s
279:	learn: 0.6127063	total: 2.92s	remaining: 7.5s
280:	learn: 0.6124807	total: 2.92s	remaining: 7.47s
281:	learn: 0.6122502	total: 2.93s	remaining: 7.46s
282:	learn: 0.6120814	total: 2.93s	remaining: 7.43s
283:	learn: 0.6118639	total: 2.94s	remaining: 7.4s
284:	learn: 0.6116363	total: 2.96s	remaining: 7.42s
285:	learn: 0.6114127	total: 2.96s	remaining: 7.39s
286:	learn: 0.6111893	total: 2.96s	remaining: 7.37s
287:	learn: 0.6109645	total: 2.97s	remaining: 7.33s
288:	learn: 0.6107401	total: 2.97s	remaining: 7.3s
289:	learn: 0.6105420	total: 2.99s	remaining: 7.32s
290:	learn: 0.6103171	total: 2.99s	remaining: 7.29s
291:	learn: 0.6100942	total: 3s	remaining: 7.26s
292:	learn: 0.6098714	total: 3s	remaining: 7.23s
293:	learn: 0.6096489	total: 3s	remaining: 7.2s
294:	learn: 0.6094280	total: 3.02s	remaining: 7.22s
295:	learn: 0.6092110	total: 3.03s	remaining: 7.2s
296:	learn: 0.6089963	tota

437:	learn: 0.5824771	total: 4.52s	remaining: 5.8s
438:	learn: 0.5823040	total: 4.52s	remaining: 5.78s
439:	learn: 0.5821296	total: 4.53s	remaining: 5.76s
440:	learn: 0.5820003	total: 4.53s	remaining: 5.74s
441:	learn: 0.5818251	total: 4.53s	remaining: 5.72s
442:	learn: 0.5816516	total: 4.54s	remaining: 5.7s
443:	learn: 0.5815248	total: 4.54s	remaining: 5.69s
444:	learn: 0.5813549	total: 4.55s	remaining: 5.67s
445:	learn: 0.5811803	total: 4.55s	remaining: 5.65s
446:	learn: 0.5810034	total: 4.6s	remaining: 5.69s
447:	learn: 0.5808334	total: 4.6s	remaining: 5.67s
448:	learn: 0.5806616	total: 4.61s	remaining: 5.65s
449:	learn: 0.5804899	total: 4.61s	remaining: 5.63s
450:	learn: 0.5803187	total: 4.61s	remaining: 5.61s
451:	learn: 0.5801490	total: 4.62s	remaining: 5.59s
452:	learn: 0.5799876	total: 4.63s	remaining: 5.59s
453:	learn: 0.5798090	total: 4.63s	remaining: 5.57s
454:	learn: 0.5796390	total: 4.63s	remaining: 5.55s
455:	learn: 0.5794733	total: 4.64s	remaining: 5.53s
456:	learn: 0.57

618:	learn: 0.5565162	total: 6.53s	remaining: 4.02s
619:	learn: 0.5563897	total: 6.58s	remaining: 4.03s
620:	learn: 0.5562619	total: 6.59s	remaining: 4.02s
621:	learn: 0.5561354	total: 6.6s	remaining: 4.01s
622:	learn: 0.5560056	total: 6.6s	remaining: 4s
623:	learn: 0.5559597	total: 6.6s	remaining: 3.98s
624:	learn: 0.5558302	total: 6.61s	remaining: 3.96s
625:	learn: 0.5557009	total: 6.61s	remaining: 3.95s
626:	learn: 0.5555778	total: 6.62s	remaining: 3.94s
627:	learn: 0.5554465	total: 6.66s	remaining: 3.94s
628:	learn: 0.5553198	total: 6.67s	remaining: 3.93s
629:	learn: 0.5551917	total: 6.67s	remaining: 3.92s
630:	learn: 0.5550688	total: 6.68s	remaining: 3.9s
631:	learn: 0.5549444	total: 6.69s	remaining: 3.9s
632:	learn: 0.5548166	total: 6.69s	remaining: 3.88s
633:	learn: 0.5547715	total: 6.69s	remaining: 3.86s
634:	learn: 0.5546440	total: 6.7s	remaining: 3.85s
635:	learn: 0.5545178	total: 6.7s	remaining: 3.83s
636:	learn: 0.5544002	total: 6.7s	remaining: 3.82s
637:	learn: 0.5542755	t

790:	learn: 0.5381575	total: 8.97s	remaining: 2.37s
791:	learn: 0.5380618	total: 8.99s	remaining: 2.36s
792:	learn: 0.5379648	total: 8.99s	remaining: 2.35s
793:	learn: 0.5379311	total: 8.99s	remaining: 2.33s
794:	learn: 0.5378341	total: 9s	remaining: 2.32s
795:	learn: 0.5377310	total: 9.02s	remaining: 2.31s
796:	learn: 0.5376596	total: 9.02s	remaining: 2.3s
797:	learn: 0.5375528	total: 9.06s	remaining: 2.29s
798:	learn: 0.5374538	total: 9.06s	remaining: 2.28s
799:	learn: 0.5373743	total: 9.08s	remaining: 2.27s
800:	learn: 0.5373034	total: 9.09s	remaining: 2.26s
801:	learn: 0.5372047	total: 9.09s	remaining: 2.24s
802:	learn: 0.5371062	total: 9.09s	remaining: 2.23s
803:	learn: 0.5370042	total: 9.09s	remaining: 2.22s
804:	learn: 0.5369033	total: 9.1s	remaining: 2.2s
805:	learn: 0.5368063	total: 9.1s	remaining: 2.19s
806:	learn: 0.5367734	total: 9.1s	remaining: 2.18s
807:	learn: 0.5366781	total: 9.11s	remaining: 2.16s
808:	learn: 0.5365805	total: 9.11s	remaining: 2.15s
809:	learn: 0.536547

950:	learn: 0.5247820	total: 10.4s	remaining: 535ms
951:	learn: 0.5247045	total: 10.4s	remaining: 524ms
952:	learn: 0.5246274	total: 10.4s	remaining: 513ms
953:	learn: 0.5245498	total: 10.4s	remaining: 502ms
954:	learn: 0.5244755	total: 10.5s	remaining: 493ms
955:	learn: 0.5243967	total: 10.5s	remaining: 481ms
956:	learn: 0.5243175	total: 10.5s	remaining: 470ms
957:	learn: 0.5242382	total: 10.5s	remaining: 459ms
958:	learn: 0.5241579	total: 10.5s	remaining: 449ms
959:	learn: 0.5240806	total: 10.5s	remaining: 438ms
960:	learn: 0.5240036	total: 10.5s	remaining: 427ms
961:	learn: 0.5239183	total: 10.5s	remaining: 415ms
962:	learn: 0.5238434	total: 10.5s	remaining: 404ms
963:	learn: 0.5237668	total: 10.5s	remaining: 393ms
964:	learn: 0.5237417	total: 10.5s	remaining: 382ms
965:	learn: 0.5236632	total: 10.5s	remaining: 371ms
966:	learn: 0.5236386	total: 10.5s	remaining: 360ms
967:	learn: 0.5235621	total: 10.5s	remaining: 348ms
968:	learn: 0.5234898	total: 10.6s	remaining: 338ms
969:	learn: 

In [28]:
best_params = {'depth': 3, 'iterations': 1000, 'learning_rate': 0.001, 'l2_leaf_reg': 3, 'border_count': 50, 'thread_count': 4}


In [29]:
# clf = RandomForestClassifier()
clf = CatBoostClassifier(loss_function='MultiClass', **best_params)

In [30]:
clf.fit(X_train, y_train,cat_features=categorical_features_indices)
clf.fit()
# score = clf.score(X_test, y_test)
# score

0:	learn: 0.6927803	total: 1.98ms	remaining: 1.98s
1:	learn: 0.6923998	total: 4.3ms	remaining: 2.14s
2:	learn: 0.6920213	total: 6.55ms	remaining: 2.18s
3:	learn: 0.6916440	total: 8.85ms	remaining: 2.2s
4:	learn: 0.6912728	total: 11.3ms	remaining: 2.25s
5:	learn: 0.6908882	total: 13.8ms	remaining: 2.28s
6:	learn: 0.6905143	total: 16ms	remaining: 2.27s
7:	learn: 0.6901341	total: 18.5ms	remaining: 2.29s
8:	learn: 0.6897671	total: 20.8ms	remaining: 2.29s
9:	learn: 0.6893854	total: 22.4ms	remaining: 2.22s
10:	learn: 0.6890167	total: 24.7ms	remaining: 2.22s
11:	learn: 0.6886576	total: 27ms	remaining: 2.23s
12:	learn: 0.6882869	total: 29ms	remaining: 2.2s
13:	learn: 0.6879081	total: 30.6ms	remaining: 2.15s
14:	learn: 0.6875367	total: 32.4ms	remaining: 2.12s
15:	learn: 0.6871629	total: 34.2ms	remaining: 2.1s
16:	learn: 0.6867912	total: 36.5ms	remaining: 2.11s
17:	learn: 0.6866263	total: 37.3ms	remaining: 2.03s
18:	learn: 0.6862595	total: 40ms	remaining: 2.06s
19:	learn: 0.6859844	total: 41.7ms

231:	learn: 0.6225002	total: 379ms	remaining: 1.25s
232:	learn: 0.6222437	total: 380ms	remaining: 1.25s
233:	learn: 0.6219877	total: 382ms	remaining: 1.25s
234:	learn: 0.6217393	total: 383ms	remaining: 1.25s
235:	learn: 0.6214922	total: 385ms	remaining: 1.25s
236:	learn: 0.6212375	total: 387ms	remaining: 1.25s
237:	learn: 0.6209850	total: 389ms	remaining: 1.25s
238:	learn: 0.6207372	total: 391ms	remaining: 1.25s
239:	learn: 0.6204839	total: 392ms	remaining: 1.24s
240:	learn: 0.6202311	total: 394ms	remaining: 1.24s
241:	learn: 0.6199787	total: 395ms	remaining: 1.24s
242:	learn: 0.6197392	total: 398ms	remaining: 1.24s
243:	learn: 0.6194905	total: 400ms	remaining: 1.24s
244:	learn: 0.6192406	total: 401ms	remaining: 1.24s
245:	learn: 0.6189900	total: 403ms	remaining: 1.23s
246:	learn: 0.6188838	total: 404ms	remaining: 1.23s
247:	learn: 0.6186286	total: 406ms	remaining: 1.23s
248:	learn: 0.6183943	total: 409ms	remaining: 1.23s
249:	learn: 0.6181539	total: 411ms	remaining: 1.23s
250:	learn: 

454:	learn: 0.5768735	total: 758ms	remaining: 908ms
455:	learn: 0.5766928	total: 760ms	remaining: 907ms
456:	learn: 0.5765228	total: 762ms	remaining: 906ms
457:	learn: 0.5763516	total: 764ms	remaining: 904ms
458:	learn: 0.5761805	total: 766ms	remaining: 903ms
459:	learn: 0.5760056	total: 767ms	remaining: 900ms
460:	learn: 0.5758333	total: 769ms	remaining: 899ms
461:	learn: 0.5756590	total: 770ms	remaining: 896ms
462:	learn: 0.5755878	total: 771ms	remaining: 894ms
463:	learn: 0.5754162	total: 772ms	remaining: 892ms
464:	learn: 0.5752504	total: 774ms	remaining: 891ms
465:	learn: 0.5751796	total: 775ms	remaining: 889ms
466:	learn: 0.5750065	total: 777ms	remaining: 887ms
467:	learn: 0.5748337	total: 778ms	remaining: 885ms
468:	learn: 0.5746662	total: 781ms	remaining: 884ms
469:	learn: 0.5745959	total: 782ms	remaining: 881ms
470:	learn: 0.5744238	total: 783ms	remaining: 879ms
471:	learn: 0.5742520	total: 784ms	remaining: 877ms
472:	learn: 0.5741821	total: 785ms	remaining: 875ms
473:	learn: 

659:	learn: 0.5478371	total: 1.13s	remaining: 584ms
660:	learn: 0.5477104	total: 1.14s	remaining: 583ms
661:	learn: 0.5475840	total: 1.14s	remaining: 581ms
662:	learn: 0.5474593	total: 1.14s	remaining: 579ms
663:	learn: 0.5473382	total: 1.14s	remaining: 578ms
664:	learn: 0.5472016	total: 1.14s	remaining: 576ms
665:	learn: 0.5470760	total: 1.14s	remaining: 574ms
666:	learn: 0.5469489	total: 1.15s	remaining: 572ms
667:	learn: 0.5468321	total: 1.15s	remaining: 571ms
668:	learn: 0.5467095	total: 1.15s	remaining: 569ms
669:	learn: 0.5465847	total: 1.15s	remaining: 568ms
670:	learn: 0.5464623	total: 1.15s	remaining: 566ms
671:	learn: 0.5463424	total: 1.16s	remaining: 565ms
672:	learn: 0.5462216	total: 1.16s	remaining: 563ms
673:	learn: 0.5461001	total: 1.16s	remaining: 562ms
674:	learn: 0.5459706	total: 1.16s	remaining: 560ms
675:	learn: 0.5458486	total: 1.17s	remaining: 558ms
676:	learn: 0.5457293	total: 1.17s	remaining: 557ms
677:	learn: 0.5456427	total: 1.17s	remaining: 556ms
678:	learn: 

862:	learn: 0.5272900	total: 1.51s	remaining: 240ms
863:	learn: 0.5272096	total: 1.51s	remaining: 238ms
864:	learn: 0.5271214	total: 1.51s	remaining: 236ms
865:	learn: 0.5270871	total: 1.51s	remaining: 234ms
866:	learn: 0.5269966	total: 1.52s	remaining: 233ms
867:	learn: 0.5269073	total: 1.52s	remaining: 231ms
868:	learn: 0.5268171	total: 1.52s	remaining: 229ms
869:	learn: 0.5267269	total: 1.52s	remaining: 227ms
870:	learn: 0.5266365	total: 1.52s	remaining: 226ms
871:	learn: 0.5265454	total: 1.53s	remaining: 224ms
872:	learn: 0.5264511	total: 1.53s	remaining: 222ms
873:	learn: 0.5264173	total: 1.53s	remaining: 221ms
874:	learn: 0.5263313	total: 1.53s	remaining: 219ms
875:	learn: 0.5262431	total: 1.53s	remaining: 217ms
876:	learn: 0.5261574	total: 1.54s	remaining: 215ms
877:	learn: 0.5260665	total: 1.54s	remaining: 214ms
878:	learn: 0.5260045	total: 1.54s	remaining: 212ms
879:	learn: 0.5259186	total: 1.54s	remaining: 210ms
880:	learn: 0.5258281	total: 1.54s	remaining: 209ms
881:	learn: 

TypeError: fit() missing 1 required positional argument: 'X'

In [ ]:
y_test_pred = clf.predict(X_test)
y_test_pred = [i[0] for i in y_test_pred]
(y_test_pred == y_test.values).mean()

In [ ]:
y_pred_train = clf.predict(X)
(y_pred_train == y.values).mean()
# y_pred_train.values


In [ ]:
y_test_pred = clf.predict(X_test)
(y_test_pred == y_test.values).mean()

In [ ]:
y_test.values

In [31]:
clf.fit(X, y, cat_features=categorical_features_indices)


0:	learn: 0.6927780	total: 2.39ms	remaining: 2.39s
1:	learn: 0.6924005	total: 4.68ms	remaining: 2.34s
2:	learn: 0.6920204	total: 5.89ms	remaining: 1.96s
3:	learn: 0.6916404	total: 7.6ms	remaining: 1.89s
4:	learn: 0.6912705	total: 10.6ms	remaining: 2.11s
5:	learn: 0.6908948	total: 12.6ms	remaining: 2.09s
6:	learn: 0.6905104	total: 14.5ms	remaining: 2.06s
7:	learn: 0.6901301	total: 16.2ms	remaining: 2s
8:	learn: 0.6897610	total: 17.8ms	remaining: 1.96s
9:	learn: 0.6893859	total: 18.9ms	remaining: 1.87s
10:	learn: 0.6890116	total: 20.1ms	remaining: 1.81s
11:	learn: 0.6886498	total: 21.8ms	remaining: 1.79s
12:	learn: 0.6882860	total: 23.4ms	remaining: 1.77s
13:	learn: 0.6879138	total: 24.8ms	remaining: 1.75s
14:	learn: 0.6875572	total: 26.5ms	remaining: 1.74s
15:	learn: 0.6871952	total: 28.9ms	remaining: 1.78s
16:	learn: 0.6868279	total: 31ms	remaining: 1.79s
17:	learn: 0.6864619	total: 33.2ms	remaining: 1.81s
18:	learn: 0.6860996	total: 35.1ms	remaining: 1.81s
19:	learn: 0.6857315	total: 

213:	learn: 0.6267063	total: 382ms	remaining: 1.4s
214:	learn: 0.6264489	total: 383ms	remaining: 1.4s
215:	learn: 0.6262491	total: 384ms	remaining: 1.4s
216:	learn: 0.6259925	total: 386ms	remaining: 1.39s
217:	learn: 0.6257385	total: 388ms	remaining: 1.39s
218:	learn: 0.6254841	total: 389ms	remaining: 1.39s
219:	learn: 0.6252280	total: 391ms	remaining: 1.39s
220:	learn: 0.6249733	total: 392ms	remaining: 1.38s
221:	learn: 0.6247746	total: 394ms	remaining: 1.38s
222:	learn: 0.6245207	total: 395ms	remaining: 1.38s
223:	learn: 0.6242672	total: 396ms	remaining: 1.37s
224:	learn: 0.6240112	total: 398ms	remaining: 1.37s
225:	learn: 0.6237540	total: 399ms	remaining: 1.37s
226:	learn: 0.6235058	total: 401ms	remaining: 1.36s
227:	learn: 0.6233103	total: 402ms	remaining: 1.36s
228:	learn: 0.6230583	total: 404ms	remaining: 1.36s
229:	learn: 0.6228134	total: 406ms	remaining: 1.36s
230:	learn: 0.6225697	total: 408ms	remaining: 1.36s
231:	learn: 0.6223151	total: 410ms	remaining: 1.36s
232:	learn: 0.6

438:	learn: 0.5795554	total: 761ms	remaining: 973ms
439:	learn: 0.5794205	total: 762ms	remaining: 970ms
440:	learn: 0.5792850	total: 764ms	remaining: 969ms
441:	learn: 0.5791120	total: 766ms	remaining: 967ms
442:	learn: 0.5789353	total: 768ms	remaining: 966ms
443:	learn: 0.5787647	total: 770ms	remaining: 964ms
444:	learn: 0.5785918	total: 771ms	remaining: 962ms
445:	learn: 0.5784234	total: 773ms	remaining: 960ms
446:	learn: 0.5782901	total: 774ms	remaining: 957ms
447:	learn: 0.5781194	total: 775ms	remaining: 955ms
448:	learn: 0.5779476	total: 777ms	remaining: 953ms
449:	learn: 0.5777761	total: 778ms	remaining: 951ms
450:	learn: 0.5776048	total: 780ms	remaining: 949ms
451:	learn: 0.5774339	total: 781ms	remaining: 947ms
452:	learn: 0.5772632	total: 783ms	remaining: 945ms
453:	learn: 0.5770929	total: 784ms	remaining: 943ms
454:	learn: 0.5769188	total: 786ms	remaining: 942ms
455:	learn: 0.5767495	total: 788ms	remaining: 940ms
456:	learn: 0.5765768	total: 790ms	remaining: 938ms
457:	learn: 

640:	learn: 0.5503199	total: 1.14s	remaining: 638ms
641:	learn: 0.5501946	total: 1.14s	remaining: 637ms
642:	learn: 0.5500734	total: 1.14s	remaining: 635ms
643:	learn: 0.5499412	total: 1.15s	remaining: 634ms
644:	learn: 0.5498174	total: 1.15s	remaining: 632ms
645:	learn: 0.5496950	total: 1.15s	remaining: 630ms
646:	learn: 0.5495732	total: 1.15s	remaining: 629ms
647:	learn: 0.5494500	total: 1.15s	remaining: 627ms
648:	learn: 0.5493245	total: 1.16s	remaining: 625ms
649:	learn: 0.5492017	total: 1.16s	remaining: 623ms
650:	learn: 0.5491078	total: 1.16s	remaining: 622ms
651:	learn: 0.5489812	total: 1.16s	remaining: 620ms
652:	learn: 0.5488542	total: 1.17s	remaining: 619ms
653:	learn: 0.5487322	total: 1.17s	remaining: 617ms
654:	learn: 0.5486084	total: 1.17s	remaining: 616ms
655:	learn: 0.5484868	total: 1.17s	remaining: 614ms
656:	learn: 0.5483654	total: 1.17s	remaining: 613ms
657:	learn: 0.5482442	total: 1.18s	remaining: 611ms
658:	learn: 0.5481232	total: 1.18s	remaining: 609ms
659:	learn: 

798:	learn: 0.5334447	total: 1.52s	remaining: 381ms
799:	learn: 0.5333697	total: 1.52s	remaining: 380ms
800:	learn: 0.5332765	total: 1.52s	remaining: 378ms
801:	learn: 0.5331830	total: 1.53s	remaining: 377ms
802:	learn: 0.5331097	total: 1.53s	remaining: 375ms
803:	learn: 0.5330138	total: 1.53s	remaining: 373ms
804:	learn: 0.5329182	total: 1.53s	remaining: 371ms
805:	learn: 0.5328231	total: 1.53s	remaining: 369ms
806:	learn: 0.5327242	total: 1.54s	remaining: 367ms
807:	learn: 0.5326298	total: 1.54s	remaining: 366ms
808:	learn: 0.5325572	total: 1.54s	remaining: 364ms
809:	learn: 0.5324565	total: 1.54s	remaining: 362ms
810:	learn: 0.5323619	total: 1.54s	remaining: 360ms
811:	learn: 0.5322694	total: 1.55s	remaining: 358ms
812:	learn: 0.5321748	total: 1.55s	remaining: 356ms
813:	learn: 0.5320813	total: 1.55s	remaining: 354ms
814:	learn: 0.5319870	total: 1.55s	remaining: 352ms
815:	learn: 0.5319024	total: 1.55s	remaining: 350ms
816:	learn: 0.5318086	total: 1.55s	remaining: 348ms
817:	learn: 

986:	learn: 0.5181331	total: 1.9s	remaining: 25ms
987:	learn: 0.5180589	total: 1.9s	remaining: 23.1ms
988:	learn: 0.5179838	total: 1.9s	remaining: 21.2ms
989:	learn: 0.5179050	total: 1.91s	remaining: 19.2ms
990:	learn: 0.5178368	total: 1.91s	remaining: 17.3ms
991:	learn: 0.5177670	total: 1.91s	remaining: 15.4ms
992:	learn: 0.5176947	total: 1.91s	remaining: 13.5ms
993:	learn: 0.5176388	total: 1.92s	remaining: 11.6ms
994:	learn: 0.5175641	total: 1.92s	remaining: 9.64ms
995:	learn: 0.5174970	total: 1.92s	remaining: 7.71ms
996:	learn: 0.5174438	total: 1.92s	remaining: 5.78ms
997:	learn: 0.5173732	total: 1.92s	remaining: 3.85ms
998:	learn: 0.5173028	total: 1.93s	remaining: 1.93ms
999:	learn: 0.5172424	total: 1.93s	remaining: 0us


In [32]:
df_pred = pd.read_csv("../data/test.csv")
# df_pred[df_pred["Dependents"] == "3+"] = "3"
# df_pred[df_pred["Dependents"].isnull()] = "0"
# df_pred["Dependents"] = df_pred["Dependents"].astype(int)
# df_pred[df_pred["Credit_History"].isnull()] = "0"
# df["Credit_History"] = df["Credit_History"].astype(int)
df_pred = df_pred.fillna(df_pred.mean())
df_pred = df_pred.fillna(df_pred.mode().iloc[0])

# X_pred = df_pred[features]
X_pred = df_pred.drop(["Loan_ID"], axis=1)
y_pred = clf.predict(X_pred)
df_pred["Loan_Status"] = y_pred
df_submission = df_pred[["Loan_ID", "Loan_Status"]]
df_submission.to_csv("../data/pred.csv", index=False)

In [ ]:
df_pred = df_pred.fillna(df_pred.mode().iloc[0])
df_pred.isnull().sum()

In [ ]:
# from sklearn.neural_network import MLPClassifier
# from sklearn.neighbors import KNeighborsClassifier
# from sklearn.svm import SVC
# from sklearn.gaussian_process import GaussianProcessClassifier
# from sklearn.gaussian_process.kernels import RBF
# from sklearn.tree import DecisionTreeClassifier
# from sklearn.ensemble import RandomForestClassifier, AdaBoostClassifier
# from sklearn.naive_bayes import GaussianNB
# from sklearn.discriminant_analysis import QuadraticDiscriminantAnalysis

# import lightgbm
# import xgboost

In [ ]:
# names = ["Nearest Neighbors", "Linear SVM", "RBF SVM", "Gaussian Process",
#          "Decision Tree", "Random Forest", "Neural Net", "AdaBoost",
#          "Naive Bayes", "QDA"]

# classifiers = [
#     KNeighborsClassifier(3),
#     SVC(kernel="linear", C=0.025),
#     SVC(gamma=2, C=1),
#     GaussianProcessClassifier(1.0 * RBF(1.0)),
#     DecisionTreeClassifier(max_depth=5),
#     RandomForestClassifier(max_depth=5, n_estimators=10, max_features=1),
#     MLPClassifier(alpha=1, max_iter=1000),
#     AdaBoostClassifier(),
#     GaussianNB(),
#     QuadraticDiscriminantAnalysis()]

In [ ]:
# for name, classifier in zip(names, classifiers):
#     clf.fit(X_train, y_train)
#     score = clf.score(X_test, y_test)
#     print(f"{name}: {score}")